# Find SGLs Notebook Managed

The whole point of this notebook is that there are very few colocalization so why am I bothering with making scripts
that are run through qsub??

In [148]:
import os 
import glob
import sys
import pybedtools as pbt
import pandas as pd
import numpy as np
import subprocess as sp
import json
import argparse
from itertools import chain
pbt.helpers.set_tempdir('/mnt/BioHome/jreyna/tmp/')
pbt.set_bedtools_path('/mnt/BioApps/bedtools/bin/')
bgzip = '/mnt/BioApps/tabix/tabix-0.2.6/bgzip'
tabix = '/mnt/BioApps/tabix/tabix-0.2.6/tabix'

pd.options.display.max_columns = 1000
pd.options.display.max_rows = 1000
pd.set_option('display.max_columns', 1000)
pd.set_option('display.max_colwidth', 400)

In [149]:
os.chdir('/mnt/BioHome/jreyna/jreyna/projects/dchallenge/')

In [150]:
# setting basical column names for bedpe
bedpe_6cols = ['chrA', 'startA', 'endA', 'chrB', 'startB', 'endB']
bedpe_10cols = ['chrA', 'startA', 'endA', 'chrB', 'startB', 'endB', 'name', 'score', 'strandA', 'strandB']

In [151]:
# pathing a few reference files
gs = 'results/refs/hg19/hg19.chrom.sizes'
gene_ref = 'results/refs/gencode/v30/gencode.v30.annotation.grch37.genes_only.bed'
outdir = 'results/main/GRCh37/sgls/notebook_output/Find_SGLs.Notebook_Managed.LD_SNPs_ARE_Included/'
os.makedirs(outdir, exist_ok=True)

## Loading the Gencode Information

In [152]:
gencode = pd.read_table(gene_ref, header=None)
gencode.columns = ['chr', 'gene_start', 'gene_end', 'gene_strand', 'type', 'geneid', 'genename']

## Loading the COLOC data

In [153]:
#eqtls = 'results/main/GRCh37/sgls/ImmuNexUT/T1D_34012112_Gaulton/ImmuNexUT/DN_B/eqtls.coloc_filtered.tsv.gz'

colocs = 'results/main/GRCh37/coloc/*/*/*/*/ldpairs/coloc_ld_snps.txt'
colocs = glob.glob(colocs)

In [154]:
len(colocs)

165

In [155]:
data = []
for fn in colocs:
    
    # get data source
    file_info = fn.split('/')  
    gwas_source = file_info[5]
    eqtl_source = file_info[6]
    ge_source = file_info[7]
    
    # load the data
    df = pd.read_table(fn)
    df['gwas_source'] = gwas_source
    df['eqtl_source'] = eqtl_source
    df['ge_source'] = ge_source
    data.append(df)
    
colocs_df = pd.concat(data)

In [156]:
colocs_df['coloc_pos'] = colocs_df['pos']
colocs_df['pos'] = colocs_df['ld_pos']

In [157]:
colocs_df.shape

(12066, 35)

In [158]:
# add snp_start and snp_end
colocs_df.loc[:, 'snp_start'] = colocs_df['pos'] - 1
colocs_df.loc[:, 'snp_end'] = colocs_df['pos']

In [159]:
colocs_df.rename(columns = {'geneName': 'geneid_versioned'}, inplace=True)
colocs_df.loc[:, 'geneid'] = colocs_df['geneid_versioned'].str.replace('\.[0-9]+$', '', regex=True)

In [160]:
# add gene meta data
colocs_df = colocs_df.merge(gencode.drop(['chr', 'type'], axis=1),
                            left_on='geneid', right_on='geneid')

In [164]:
colocs_df.loc[colocs_df.genename == 'IL2RA']

chr      pos  pp_H0_Coloc_Summary  pp_H1_Coloc_Summary  \
4896  chr10  6114010        4.940656e-324        2.661698e-300   
4897  chr10  6113782        4.940656e-324        2.661698e-300   
4898  chr10  6110829        4.940656e-324        2.661698e-300   
4899  chr10  6110875        4.940656e-324        2.661698e-300   
4900  chr10  6114010         0.000000e+00         0.000000e+00   
4901  chr10  6113782         0.000000e+00         0.000000e+00   
4902  chr10  6110829         0.000000e+00         0.000000e+00   
4903  chr10  6110875         0.000000e+00         0.000000e+00   
4904  chr10  6114010         0.000000e+00         0.000000e+00   
4905  chr10  6113782         0.000000e+00         0.000000e+00   
4906  chr10  6110829         0.000000e+00         0.000000e+00   
4907  chr10  6110875         0.000000e+00         0.000000e+00   
4908  chr10  6114293         0.000000e+00         0.000000e+00   
4909  chr10  6096158         0.000000e+00         0.000000e+00   
4910  chr10  6120051         0.000000e+00         0.000000e+00   
4911  chr10  6098824         0.000000e+00         0.000000e+00   
4912  chr10  6118127         0.000000e+00         0.000000e+00   
4913  chr10  6114010        5.187654e-301        8.284947e-300   
4914  chr10  6113782        5.187654e-301        8.284947e-300   
4915  chr10  6110829        5.187654e-301        8.284947e-300   
4916  chr10  6110875        5.187654e-301        8.284947e-300   
4917  chr10  6114010         6.885934e-25         1.168451e-23   
4918  chr10  6113782         6.885934e-25         1.168451e-23   
4919  chr10  6110829         6.885934e-25         1.168451e-23   
4920  chr10  6110875         6.885934e-25         1.168451e-23   

      pp_H2_Coloc_Summary  pp_H3_Coloc_Summary  pp_H4_Coloc_Summary  \
4896         2.472479e-26             0.015565             0.984435   
4897         2.472479e-26             0.015565             0.984435   
4898         2.472479e-26             0.015565             0.984435   
4899         2.472479e-26             0.015565             0.984435   
4900         2.475039e-26             0.014546             0.985454   
4901         2.475039e-26             0.014546             0.985454   
4902         2.475039e-26             0.014546             0.985454   
4903         2.475039e-26             0.014546             0.985454   
4904         3.289313e-03             0.048300             0.948410   
4905         3.289313e-03             0.048300             0.948410   
4906         3.289313e-03             0.048300             0.948410   
4907         3.289313e-03             0.048300             0.948410   
4908         7.329628e-03             0.116181             0.876489   
4909         7.329628e-03             0.116181             0.876489   
4910         7.329628e-03             0.116181             0.876489   
4911         7.329628e-03             0.116181             0.876489   
4912         7.329628e-03             0.116181             0.876489   
4913         3.278549e-03             0.051415             0.945307   
4914         3.278549e-03             0.051415             0.945307   
4915         3.278549e-03             0.051415             0.945307   
4916         3.278549e-03             0.051415             0.945307   
4917         3.268014e-03             0.054512             0.942220   
4918         3.268014e-03             0.054512             0.942220   
4919         3.268014e-03             0.054512             0.942220   
4920         3.268014e-03             0.054512             0.942220   

          rs_id      variant_id    geneid_versioned  dist        pvalue  \
4896  rs7090530  10:6068912:C:A  ENSG00000134460.15  6587  2.433710e-20   
4897  rs7090530  10:6068912:C:A  ENSG00000134460.15  6587  2.433710e-20   
4898  rs7090530  10:6068912:C:A  ENSG00000134460.15  6587  2.433710e-20   
4899  rs7090530  10:6068912:C:A  ENSG00000134460.15  6587  2.433710e-20   
4900  rs7090530  10:6068912:C:A  ENSG00000134460.15  6587  5.046700e-

In [89]:
# add a coloc idd
def get_coloc_id(sr):
    s = '{}.{}.{}.{}.{}.{}'.format(sr.chr, sr.pos, sr.genename, sr.gwas_source, sr.eqtl_source, sr.ge_source)
    return(s)
colocs_df.loc[:, 'coloc_id'] = colocs_df.apply(get_coloc_id, axis=1)

# create a pybedtools object
colocs_gene_bedpe = colocs_df.loc[:, ['chr', 'snp_start', 'snp_end', 'chr', 'gene_start', 'gene_end', 'coloc_id']]
colocs_gene_pbt = pbt.BedTool.from_dataframe(colocs_gene_bedpe)

In [90]:
def get_tss_cords(sr):
    if sr.gene_strand == '+':
        return([sr.gene_start, sr.gene_start + 1])
    else:
        return([sr.gene_end - 1, sr.gene_end])
tss_starts, tss_ends = list(zip(*colocs_df.apply(get_tss_cords, axis=1)))
colocs_df['tss_start'] = tss_starts
colocs_df['tss_end'] = tss_ends

In [91]:
# create a pybedtools object
colocs_tss_bedpe = colocs_df.loc[:, ['chr', 'snp_start', 'snp_end', 'chr', 'tss_start', 'tss_end', 'coloc_id']]
colocs_tss_pbt = pbt.BedTool.from_dataframe(colocs_tss_bedpe)

## Intersecting COLOCs with Loops

In [92]:
loops = 'results/main/h3k27ac_hichip/*/FitHiChIP_S/FitHiChIP.interactions_FitHiC_Q0.01.bed'
loops = sorted(glob.glob(loops))
loops = loops[0:3] + [loops[11]]

In [93]:
# add loop id
def get_loop_id(sr):
    s = '{}.{}.{}.{}.{}.{}'.format(sr.chr1, sr.s1, sr.e1, sr.chr2, sr.s2, sr.e2)
    return(s)

In [94]:
tss_slop = 5000
gene_slop = 0

In [95]:
compiled_sgls = []
for loop_fn in loops:
    
    # get file sources
    file_info = loop_fn.split('/')
    loop_source = file_info[3]
    
    # load the loop data
    loop_df = pd.read_table(loop_fn)
    loop_df['loop_id'] = loop_df.apply(get_loop_id, axis=1)
    loops_bedpe = loop_df[['chr1', 's1', 'e1', 'chr2', 's2', 'e2', 'loop_id']]
    loop_pbt = pbt.BedTool.from_dataframe(loops_bedpe)

    # search for loops which overlap the gene body
    whole_gene_sgls = colocs_gene_pbt.pairtopair(loop_pbt, slop=gene_slop, type='both')
    wg_sgl_tmp = whole_gene_sgls.to_dataframe(disable_auto_names=True, header=None)
    wg_sgl_tmp.dropna(how='all', axis=1, inplace=True)
    wg_sgl_tmp['sgl_kind'] = 'gene'

    # search for loops which overlap the gene tss
    tss_sgls = colocs_tss_pbt.pairtopair(loop_pbt, slop=tss_slop, type='both')
    tss_sgl_tmp = tss_sgls.to_dataframe(disable_auto_names=True, header=None)
    tss_sgl_tmp.dropna(how='all', axis=1, inplace=True)
    tss_sgl_tmp['sgl_kind'] = 'tss'

    # merge both loop types 
    if wg_sgl_tmp.shape[0] > 0:
        if tss_sgl_tmp.shape[0] > 0:
            all_sgls = pd.concat([wg_sgl_tmp, tss_sgl_tmp], axis=0)
        else:
            all_sgls = wg_sgl_tmp
    else:
        if tss_sgl_tmp.shape[0] > 0:
            all_sgls = tss_sgl_tmp
        else:
            all_sgls = []

    
    if len(all_sgls) > 0: 
                
        all_sgls.columns = colocs_gene_bedpe.columns.tolist() + \
                            ['loop_chrA', 'loop_startA', 'loop_endA', \
                            'loop_chrB', 'loop_startB', 'loop_endB', \
                            'loop_id', 'sgl_kind']
        all_sgls = all_sgls.merge(colocs_df, on='coloc_id', suffixes=(None, '_remove'))
        all_sgls = all_sgls.merge(loop_df, on='loop_id', suffixes=(None, '_remove'))
        remove_cols = [x for x in all_sgls.columns.tolist() if '_remove' in x]
        all_sgls.drop(remove_cols, axis=1, inplace=True)

        # add loop source
        all_sgls['loop_source'] = loop_source

        ## Prioritize the tss loop 
        for grp, grp_df in all_sgls.groupby(['coloc_id', 'loop_id']):    

            if grp_df.shape[0] == 1:
                compiled_sgls.append(grp_df)
            else:        
                pr = grp_df.loc[grp_df.sgl_kind == 'tss']
                compiled_sgls.append(pr)
        

In [96]:
compiled_sgls = pd.concat(compiled_sgls)

In [97]:
compiled_sgls.shape

(3239, 80)

In [98]:
compiled_sgls.genename.unique()

array(['RGS1', 'AL137186.1', 'RBM17', 'IL2RA', 'NAA25', 'TMEM116',
       'AP005137.2', 'BCL11A', 'HIST1H1A', 'DUSP22', 'MAP3K7', 'BACH2',
       'AL132996.1', 'PRKCQ', 'PRKCQ-AS1', 'CTLA4', 'TMPRSS3', 'UMODL1',
       'ABCG1', 'NDUFV3', 'NUDT6', 'BBS7', 'AL121787.1', 'ANKRD6',
       'RRAGD', 'RFX3', 'GLIS3', 'RPS26', 'AL133370.1'], dtype=object)

## Extract SGLs between matched samples only

In [99]:
sgl_samplesheet = pd.read_table('config/sgl_samplesheets/sgl.samplesheet.tsv', comment='#')
sgl_samplesheet['master_sources'] = sgl_samplesheet['gwas_source'] + ':' \
                                    + sgl_samplesheet['eqtl_source'] + ':' \
                                    + sgl_samplesheet['ge_source'] + ':' \
                                    + sgl_samplesheet['loop_source']

In [100]:
compiled_sgls['master_sources'] = compiled_sgls['gwas_source'] + ':' \
                                    + compiled_sgls['eqtl_source'] + ':' \
                                    + compiled_sgls['ge_source'] + ':' \
                                    + compiled_sgls['loop_source']
compiled_sgls['eqtl_hichip_mapped'] = compiled_sgls['master_sources'].isin(sgl_samplesheet['master_sources'])
compiled_sgls = compiled_sgls.loc[compiled_sgls['eqtl_hichip_mapped'] == True]

## Add the full id

In [101]:
compiled_sgls['full_id'] = compiled_sgls['coloc_id'] + '.' \
                            + compiled_sgls['gwas_source'] + '.' \
                            + compiled_sgls['eqtl_source'] + '.' \
                            + compiled_sgls['ge_source'] + '.' \
                            + compiled_sgls['loop_source']

## Save  unique list of genes

In [117]:
compiled_sgls_genes = sorted(set(compiled_sgls.geneid.to_list()))
comp_fn = os.path.join(outdir, 'compiled_sgls_genes.txt')
with open(comp_fn, 'w') as f:
    for gene in compiled_sgls_genes:
        f.write(gene + '\n')
print(comp_fn)

results/main/GRCh37/sgls/notebook_output/Find_SGLs.Notebook_Managed.LD_SNPs_ARE_Included/compiled_sgls_genes.txt


## add colors

In [102]:
blue_hex = '#377eb8'.upper()
green_hex = '#4daf4a'.upper()
compiled_sgls['color'] = compiled_sgls['sgl_kind'].map({'tss': green_hex, 'gene': blue_hex})

## save to file

In [103]:
sgl_washu = compiled_sgls[['chr1', 's1', 'e1']]
sgl_washu['right'] = compiled_sgls['chr2'] + ':' \
                        + compiled_sgls['s2'].astype(str) + '-' \
                        + compiled_sgls['e2'].astype(str) + ','  \
                        + compiled_sgls['pp_H4_Coloc_Summary'].astype(str)
sgl_washu['full_id'] = compiled_sgls['full_id']
sgl_washu['color'] = compiled_sgls['color']
sgl_washu['chr_int'] = sgl_washu['chr1'].str.replace('chr', '').astype(int)
sgl_washu.sort_values(['chr_int', 's1', 'e1'], inplace=True)
sgl_washu.drop(['chr_int'], axis=1, inplace=True)

/mnt/BioHome/jreyna/tmp//ipykernel_28923/522069270.py:2: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  sgl_washu['right'] = compiled_sgls['chr2'] + ':' \
/mnt/BioHome/jreyna/tmp//ipykernel_28923/522069270.py:6: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  sgl_washu['full_id'] = compiled_sgls['full_id']
/mnt/BioHome/jreyna/tmp//ipykernel_28923/522069270.py:7: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

S

In [104]:
sgl_fn = os.path.join(outdir, 'sgl.track.refbed')

In [105]:
sgl_washu.iloc[:, 0:6].to_csv(sgl_fn, sep='\t', index=False, header=False)

In [169]:
sgl_washu.loc[sgl_washu.full_id.str.contains('chr10.6110875.IL2RA')]

chr1       s1       e1                                    right  \
217  chr10  6085000  6090000  chr10:6110000-6115000,0.942220361575639   
208  chr10  6085000  6090000  chr10:6110000-6115000,0.948410334817422   
213  chr10  6085000  6090000  chr10:6110000-6115000,0.945306655980214   
204  chr10  6085000  6090000  chr10:6110000-6115000,0.985454003893149   
200  chr10  6085000  6090000  chr10:6110000-6115000,0.984434690674149   
238  chr10  6090000  6095000  chr10:6110000-6115000,0.942220361575639   
229  chr10  6090000  6095000  chr10:6110000-6115000,0.948410334817422   
234  chr10  6090000  6095000  chr10:6110000-6115000,0.945306655980214   
225  chr10  6090000  6095000  chr10:6110000-6115000,0.985454003893149   
221  chr10  6090000  6095000  chr10:6110000-6115000,0.984434690674149   
280  chr10  6095000  6100000  chr10:6110000-6115000,0.942220361575639   
262  chr10  6095000  6100000  chr10:6110000-6115000,0.948410334817422   
272  chr10  6095000  6100000  chr10:6110000-6115000,0.945306655980214   
254  chr10  6095000  6100000  chr10:6110000-6115000,0.985454003893149   
246  chr10  6095000  6100000  chr10:6110000-6115000,0.984434690674149   

                                                                                                        full_id  \
217                    chr10.6110875.IL2RA.T1D_32005708.ImmuNexUT.DN_B.T1D_32005708.ImmuNexUT.DN_B.B-cell_naive   
208                    chr10.6110875.IL2RA.T1D_32005708.ImmuNexUT.SM_B.T1D_32005708.ImmuNexUT.SM_B.B-cell_naive   
213                  chr10.6110875.IL2RA.T1D_32005708.ImmuNexUT.USM_B.T1D_32005708.ImmuNexUT.USM_B.B-cell_naive   
204    chr10.6110875.IL2RA.T1D_34012112_Gaulton.ImmuNexUT.SM_B.T1D_34012112_Gaulton.ImmuNexUT.SM_B.B-cell_naive   
200  chr10.6110875.IL2RA.T1D_34012112_Gaulton.ImmuNexUT.USM_B.T1D_34012112_Gaulton.ImmuNexUT.USM_B.B-cell_naive   
238                    chr10.6110875.IL2RA.T1D_32005708.ImmuNexUT.DN_B.T1D_32005708.ImmuNexUT.DN_B.B-cell_naive   
229                    chr10.6110875.IL2RA.T1D_32005708.ImmuNexUT.SM_B.T1D_32005708.ImmuNexUT.SM_B.B-cell_naive   
234                  chr10.6110875.IL2RA.T1D_32005708.ImmuNexUT.USM_B.T1D_32005708.ImmuNexUT.USM_B.B-cell_naive   
225    chr10.6110875.IL2RA.T1D_34012112_Gaulton.ImmuNexUT.SM_B.T1D_34012112_Gaulton.ImmuNexUT.SM_B.B-cell_naive   
221  chr10.6110875.IL2RA.T1D_34012112_Gaulton.ImmuNexUT.USM_B.T1D_34012112_Gaulton.ImmuNexUT.USM_B.B-cell_naive   
280                    chr10.6110875.IL2RA.T1D_32005708.ImmuNexUT.DN_B.T1D_32005708.ImmuNexUT.DN_B.B-cell_naive   
262                    chr10.6110875.IL2RA.T1D_32005708.ImmuNexUT.SM_B.T1D_32005708.ImmuNexUT.SM_B.B-cell_naive   
272                  chr10.6110875.IL2RA.T1D_32005708.ImmuNexUT.USM_B.T1D_32005708.ImmuNexUT.USM_B.B-cell_naive   
254    chr10.6110875.IL2RA.T1D_34012112_Gaulton.ImmuNexUT.SM_B.T1D_34012112_Gaulton.ImmuNexUT.SM_B.B-cell_naive   
246  chr10.6110875.IL2RA.T1D_34012112_Gaulton.ImmuNexUT.USM_B.T1D_34012112_Gaulton.ImmuNexUT.USM_B.B-cell_naive   

       color  
217  #377EB8  
208  #377EB8  
213  #377EB8  
204  #377EB8  
200  #377EB8  
238  #377EB8  
229  #377EB8  
234  #377EB8  
225  #377EB8  
221  #377EB8  
280  #4DAF4A  
262  #4DAF4A  
272  #4DAF4A  
254  #4DAF4A  
246  #4DAF4A

In [168]:
sgl_washu

chr1         s1         e1                                       right  \
1857   chr1  192505000  192510000  chr1:192540000-192545000,0.865499348571967   
1868   chr1  192505000  192510000  chr1:192545000-192550000,0.865499348571967   
1850   chr1  192505000  192510000  chr1:192540000-192545000,0.865499348571967   
1861   chr1  192505000  192510000  chr1:192545000-192550000,0.865499348571967   
1854   chr1  192505000  192510000  chr1:192540000-192545000,0.865499348571967   
...     ...        ...        ...                                         ...   
303   chr21   43820000   43825000   chr21:43835000-43840000,0.876223538737684   
340   chr21   43820000   43825000   chr21:43840000-43845000,0.868210562364591   
365   chr21   43820000   43825000   chr21:43845000-43850000,0.868210562364591   
343   chr21   43820000   43825000   chr21:43840000-43845000,0.876223538737684   
370   chr21   43820000   43825000   chr21:43845000-43850000,0.876223538737684   

                                                                                                                                 full_id  \
1857  chr1.192501921.RGS1.T1D_34012112_Gaulton.Schmiedel_2018.Treg_naive.T1D_34012112_Gaulton.Schmiedel_2018.Treg_naive.CD4_T-cell_naive   
1868  chr1.192501921.RGS1.T1D_34012112_Gaulton.Schmiedel_2018.Treg_naive.T1D_34012112_Gaulton.Schmiedel_2018.Treg_naive.CD4_T-cell_naive   
1850  chr1.192505757.RGS1.T1D_34012112_Gaulton.Schmiedel_2018.Treg_naive.T1D_34012112_Gaulton.Schmiedel_2018.Treg_naive.CD4_T-cell_naive   
1861  chr1.192505757.RGS1.T1D_34012112_Gaulton.Schmiedel_2018.Treg_naive.T1D_34012112_Gaulton.Schmiedel_2018.Treg_naive.CD4_T-cell_naive   
1854  chr1.192506363.RGS1.T1D_34012112_Gaulton.Schmiedel_2018.Treg_naive.T1D_34012112_Gaulton.Schmiedel_2018.Treg_naive.CD4_T-cell_naive   
...                                                                                                                                  ...   
303                            chr21.43832679.TMPRSS3.T1D_25751624.ImmuNexUT.TEMRA_CD8.T1D_25751624.ImmuNexUT.TEMRA_CD8.CD8_T-cell_naive   
340                                  chr21.43846729.TMPRSS3.T1D_25751624.ImmuNexUT.CM_CD8.T1D_25751624.ImmuNexUT.CM_CD8.CD8_T-cell_naive   
365                                  chr21.43846729.TMPRSS3.T1D_25751624.ImmuNexUT.CM_CD8.T1D_25751624.ImmuNexUT.CM_CD8.CD8_T-cell_naive   
343                            chr21.43846729.TMPRSS3.T1D_25751624.ImmuNexUT.TEMRA_CD8.T1D_25751624.ImmuNexUT.TEMRA_CD8.CD8_T-cell_naive   
370                            chr21.43846729.TMPRSS3.T1D_25751624.ImmuNexUT.TEMRA_CD8.T1D_25751624.ImmuNexUT.TEMRA_CD8.CD8_T-cell_naive   

        color  
1857  #4DAF4A  
1868  #4DAF4A  
1850  #4DAF4A  
1861  #4DAF4A  
1854  #4DAF4A  
...       ...  
303   #4DAF4A  
340   #4DAF4A  
365   #4DAF4A  
343   #4DAF4A  
370   #4DAF4A  

[1066 rows x 6 columns]

In [106]:
sgl_fn

'results/main/GRCh37/sgls/notebook_output/Find_SGLs.Notebook_Managed.LD_SNPs_ARE_Included/sgl.track.refbed'

In [107]:
cmd = 'bgzip -f {}\n'.format(sgl_fn)
cmd += 'tabix -p bed -f {}.gz'.format(sgl_fn)

In [108]:
print(cmd)

bgzip -f results/main/GRCh37/sgls/notebook_output/Find_SGLs.Notebook_Managed.LD_SNPs_ARE_Included/sgl.track.refbed
tabix -p bed -f results/main/GRCh37/sgls/notebook_output/Find_SGLs.Notebook_Managed.LD_SNPs_ARE_Included/sgl.track.refbed.gz


## View, Search and Query

In [109]:
compiled_sgls.genename

216    IL2RA
237    IL2RA
278    IL2RA
207    IL2RA
228    IL2RA
       ...  
266    CTLA4
260    CTLA4
261    CTLA4
262    CTLA4
263    CTLA4
Name: genename, Length: 1066, dtype: object

In [110]:
compiled_sgls

chr  snp_start    snp_end    chr  gene_start   gene_end  \
216  chr10    6110828    6110829  chr10     6052652    6104333   
237  chr10    6110828    6110829  chr10     6052652    6104333   
278  chr10    6110828    6110829  chr10     6104332    6104333   
207  chr10    6110828    6110829  chr10     6052652    6104333   
228  chr10    6110828    6110829  chr10     6052652    6104333   
..     ...        ...        ...    ...         ...        ...   
266   chr2  204760207  204760208   chr2   204732494  204732495   
260   chr2  204762956  204762957   chr2   204732494  204732495   
261   chr2  204763881  204763882   chr2   204732494  204732495   
262   chr2  204764417  204764418   chr2   204732494  204732495   
263   chr2  204764813  204764814   chr2   204732494  204732495   

                                                                 coloc_id  \
216                       chr10.6110829.IL2RA.T1D_32005708.ImmuNexUT.DN_B   
237                       chr10.6110829.IL2RA.T1D_32005708.ImmuNexUT.DN_B   
278                       chr10.6110829.IL2RA.T1D_32005708.ImmuNexUT.DN_B   
207                       chr10.6110829.IL2RA.T1D_32005708.ImmuNexUT.SM_B   
228                       chr10.6110829.IL2RA.T1D_32005708.ImmuNexUT.SM_B   
..                                                                    ...   
266  chr2.204760208.CTLA4.T1D_25751624.Schmiedel_2018.monocyte_CD16_naive   
260  chr2.204762957.CTLA4.T1D_25751624.Schmiedel_2018.monocyte_CD16_naive   
261  chr2.204763882.CTLA4.T1D_25751624.Schmiedel_2018.monocyte_CD16_naive   
262  chr2.204764418.CTLA4.T1D_25751624.Schmiedel_2018.monocyte_CD16_naive   
263  chr2.204764814.CTLA4.T1D_25751624.Schmiedel_2018.monocyte_CD16_naive   

    loop_chrA  loop_startA  loop_endA loop_chrB  loop_startB  loop_endB  \
216     chr10      6085000    6090000     chr10      6110000    6115000   
237     chr10      6090000    6095000     chr10      6110000    6115000   
278     chr10      6095000    6100000     chr10      6110000    6115000   
207     chr10      6085000    6090000     chr10      6110000    6115000   
228     chr10      6090000    6095000     chr10      6110000    6115000   
..        ...          ...        ...       ...          ...        ...   
266      chr2    204735000  204740000      chr2    204755000  204760000   
260      chr2    204735000  204740000      chr2    204755000  204760000   
261      chr2    204735000  204740000      chr2    204755000  204760000   
262      chr2    204735000  204740000      chr2    204755000  204760000   
263      chr2    204735000  204740000      chr2    204755000  204760000   

                                               loop_id sgl_kind        pos  \
216        chr10.6085000.6090000.chr10.6110000.6115000     gene    6110829   
237        chr10.6090000.6095000.chr10.6110000.6115000     gene    6110829   
278        chr10.6095000.6100000.chr10.6110000.6115000      tss    6110829   
207        chr10.6085000.6090000.chr10.6110000.6115000     gene    6110829   
228        chr10.6090000.6095000.chr10.6110000.6115000     gene    6110829   
..                                                 ...      ...        ...   
266  chr2.204735000.204740000.chr2.204755000.204760000      tss  204760208   
260  chr2.204735000.204740000.chr2.204755000.204760000      tss  204762957   
261  chr2.204735000.204740000.chr2.204755000.204760000      tss  204763882   
262  chr2.204735000.204740000.chr2.204755000.204760000      tss  204764418   
263  chr2.204735000.204740000.chr2.204755000.204760000      tss  204764814   

     pp_H0_Coloc_Summary  pp_H1_Coloc_Summary  pp_H2_Coloc_Summary  \
216         6.885934e-25         1.168451e-23         3.268014e-03   
237         6.885934e-25         1.168451e-23         3.268014e-03   
278         6.885934e-25         1.168451e-23         3.268014e-03   
207         0.000000e+00         0.000000e+00         3.289313e-03   
228         0.000000e+00         0.000000e+00         3.289313e-03   
..                   ...       

In [37]:
compiled_sgls.loc[compiled_sgls.genename == 'RBM17']

chr  snp_start  snp_end    chr  gene_start  gene_end  \
2229  chr10    6098948  6098949  chr10     6130997   6130998   

                                                 coloc_id loop_chrA  \
2229  chr10.6098949.RBM17.T1D_32005708.ImmuNexUT.Fr_III_T     chr10   

      loop_startA  loop_endA loop_chrB  loop_startB  loop_endB  \
2229      6090000    6095000     chr10      6130000    6135000   

                                          loop_id sgl_kind      pos  \
2229  chr10.6090000.6095000.chr10.6130000.6135000      tss  6098949   

      pp_H0_Coloc_Summary  pp_H1_Coloc_Summary  pp_H2_Coloc_Summary  \
2229         3.548610e-59         7.792553e-58             0.009328   

      pp_H3_Coloc_Summary  pp_H4_Coloc_Summary      rs_id      variant_id  \
2229             0.204057             0.786615  rs7072793  10:6064303:T:C   

        geneid_versioned   dist    pvalue       FDR  slope_snp ref alt    AC  \
2229  ENSG00000134453.15  24684  0.000032  0.003394  -0.237425   T   C  2259   

            AF    AN  slope_se_snp  slope_gwas  slope_se_gwas  pval_nominal  \
2229  0.451078  5008      0.014041      0.1605         0.0236  1.138000e-11   

      old_pos  was_converted       rsID ld_chr   ld_pos   ld_rsID        LD  \
2229  6064303              1  rs7072793  chr10  6098949  rs706778  0.942345   

       gwas_source eqtl_source ge_source  SampleSize  coloc_pos  \
2229  T1D_32005708   ImmuNexUT  Fr_III_T         NaN    6106266   

               geneid gene_strand genename  tss_start  tss_end   chr1  \
2229  ENSG00000134453           +    RBM17    6130997  6130998  chr10   

           s1       e1   chr2       s2       e2   cc  Coverage1  isPeak1  \
2229  6090000  6095000  chr10  6130000  6135000  121       3507        1   

         Bias1  Mapp1  GCContent1  RESites1  Coverage2  isPeak2     Bias2  \
2229  2.103196      0           0         0       2225        1  1.334363   

      Mapp2  GCContent2  RESites2         p  exp_cc_Bias        p_Bias  \
2229      0           0         0  0.000004    80.202423  5.570070e-07   

      dbinom_Bias  P-Value_Bias  Q-Value_Bias       loop_source  \
2229     0.000005      0.000013      0.001085  CD4_T-cell_naive   

                                        master_sources  eqtl_hichip_mapped  \
2229  T1D_32005708:ImmuNexUT:Fr_III_T:CD4_T-cell_naive                True   

                                                                                                   full_id  \
2229  chr10.6098949.RBM17.T1D_32005708.ImmuNexUT.Fr_III_T.T1D_32005708.ImmuNexUT.Fr_III_T.CD4_T-cell_naive   

        color  
2229  #4DAF4A

In [38]:
compiled_sgls.genename.unique()

array(['IL2RA', 'NAA25', 'TMEM116', 'RGS1', 'RBM17', 'TMPRSS3',
       'HIST1H1A', 'AL121787.1', 'RPS26', 'AP005137.2', 'CTLA4'],
      dtype=object)

In [39]:
compiled_sgls.geneid.unique()

array(['ENSG00000134460', 'ENSG00000111300', 'ENSG00000198270',
       'ENSG00000090104', 'ENSG00000134453', 'ENSG00000160183',
       'ENSG00000124610', 'ENSG00000226455', 'ENSG00000197728',
       'ENSG00000272703', 'ENSG00000163599'], dtype=object)

In [40]:
compiled_sgls[['genename', 'geneid']].drop_duplicates()

genename           geneid
216        IL2RA  ENSG00000134460
398        NAA25  ENSG00000111300
50       TMEM116  ENSG00000198270
1857        RGS1  ENSG00000090104
2229       RBM17  ENSG00000134453
1204     TMPRSS3  ENSG00000160183
2227    HIST1H1A  ENSG00000124610
2121  AL121787.1  ENSG00000226455
210        RPS26  ENSG00000197728
287   AP005137.2  ENSG00000272703
259        CTLA4  ENSG00000163599

In [124]:
for g in compiled_sgls['genename'].unique().tolist():
    print(g)

IL2RA
NAA25
TMEM116
RGS1
RBM17
TMPRSS3
HIST1H1A
AL121787.1
RPS26
AP005137.2
CTLA4


## Expression of Colocalized Genes With and Without Loops

In [58]:
coloc_genes = set(colocs_df.geneid.unique().tolist())
sgl_genes  = set(compiled_sgls.geneid.unique().tolist())
coloc_only_genes = coloc_genes.difference(sgl_genes)

In [52]:
diceweb_to_loop_names = {'B_CELL_NAIVE': 'NB',
                        'MONOCYTES': 'CM',
                        'NK': 'NK',
                        'CD4_NAIVE': 'CD4N',
                        'CD8_NAIVE': 'CD8N'}

In [55]:
expr_data = []
for dice_cline, loop_cline in diceweb_to_loop_names.items():

    fn = 'results/main/dice_gene_expression/{}_TPM.csv'.format(loop_cline)
    df = pd.read_csv(fn)
    df.index = df.Feature_name.str.replace('\.[0-9]+', '', regex=True)
    df.drop(['Feature_name', 'Transcript_Length(bp)', 'Additional_annotations'], axis=1, inplace=True)
    df.loc[:, 'cline'] = loop_cline
    expr_data.append(df)   
    
expr_df = pd.concat(expr_data)

results/main/dice_gene_expression/NB_TPM.csv
results/main/dice_gene_expression/CM_TPM.csv
results/main/dice_gene_expression/NK_TPM.csv
results/main/dice_gene_expression/CD4N_TPM.csv
results/main/dice_gene_expression/CD8N_TPM.csv


In [68]:
coloc_expr_df = expr_df.loc[expr_df.index.isin(coloc_only_genes)]
coloc_expr_df['type'] = 'coloc'
sgl_expr_df = expr_df.loc[expr_df.index.isin(sgl_genes)]
sgl_expr_df['type'] = 'sgl'
compare_df = pd.concat([coloc_expr_df, sgl_expr_df])

/mnt/BioHome/jreyna/tmp//ipykernel_28923/4235081952.py:2: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  coloc_expr_df['type'] = 'coloc'
/mnt/BioHome/jreyna/tmp//ipykernel_28923/4235081952.py:4: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  sgl_expr_df['type'] = 'sgl'


In [69]:
compare_df

0           1           2           3           4  \
Feature_name                                                                  
ENSG00000004866    1.477158    1.228522    0.954731    0.834564    0.806592   
ENSG00000025039    2.821166    2.643562    2.456848    2.320778    2.198963   
ENSG00000026950  235.245405  226.275791  221.714012  209.529563  209.108815   
ENSG00000065675    1.092529    1.020098    0.948681    0.853269    0.568559   
ENSG00000079739   13.691564   13.387624   12.960432   12.785308   12.757444   
ENSG00000080298   36.145947   36.105101   35.353010   34.646030   32.430159   
ENSG00000081026    2.026828    1.159936    1.116276    0.970435    0.938531   
ENSG00000089022   28.483846   26.938844   26.770207   26.567418   26.432153   
ENSG00000096433  106.765367   99.444632   96.530323   96.463178   93.937802   
ENSG00000106686    0.919483    0.884847    0.860963    0.797260    0.779396   
ENSG00000107249    0.028137    0.028069    0.000000    0.000000    0.000000   
ENSG00000107796    5.670728    5.659299    5.637337    5.529509    5.522897   
ENSG00000110665  163.908274  156.108806  124.275407  118.136137  115.257570   
ENSG00000111231   16.448997   15.557383   12.075021   11.642143   11.637107   
ENSG00000111275    8.393630    7.750443    7.712299    7.701888    7.592749   
ENSG00000111802   63.990051   63.338166   62.567352   61.277984   60.599849   
ENSG00000111886   31.589619   18.750681   15.274571   15.059778   13.931797   
ENSG00000112182  339.309849  324.581740  322.543162  320.772079  305.837268   
ENSG00000112293    5.769111    5.381150    5.196450    4.606327    4.383068   
ENSG00000112312   11.861967   10.921975   10.046572   10.022819    9.079499   
ENSG00000112679  129.236326  128.688319  126.826483  125.131311  120.269044   
ENSG00000115421   37.158713   37.077836   35.738083   34.974771   34.058619   
ENSG00000119866  142.909793  131.478191  131.173091  126.645427  126.225706   
ENSG00000124508  113.321745  110.152844  110.082968   97.690512   95.285677   
ENSG00000128534  109.016716  101.258497   96.861194   96.735508   94.640394   
ENSG00000132436   53.305219   48.325893   45.928951   42.490728   41.940927   
ENSG00000133466   33.376542   32.896560   32.120393   29.778873   29.104598   
ENSG00000134242  177.158906  160.580860  158.389564  149.278875  145.045634   
ENSG00000135299    3.259571    2.704862    2.626511    2.596018    2.542791   
ENSG00000135341   51.111087   50.001180   49.655038   49.063196   47.644855   
ENSG00000136982    4.203182    3.497860    3.084255    3.015868    2.725169   
ENSG00000138685    2.999023    2.449939    2.229621    1.462329    1.276703   
ENSG00000138686   19.253795   16.229995   15.771540   15.692691   15.690665   
ENSG00000139531    4.077676    3.882161    3.496302    3.435453    3.274549   
ENSG00000141956   16.243744   14.646146   14.607680   14.436469   14.339312   
ENSG00000146281   60.631776   58.282220   56.968573   55.104189   54.892180   
ENSG00000150637    0.806597    0.760199    0.675722    0.627614    0.614267   
ENSG00000152766    0.366447    0.346577    0.256330    0.184807    0.178232   
ENSG00000157617   19.813242   17.913322   17.510008   17.493054   17.178162   
ENSG00000158966    0.906131    0.695685    0.640453    0.606033    0.574121   
ENSG00000160179   63.006539   50.920611   48.826939   47.787770   47.565491   
ENSG00000160181    1.189608    1.026941    0.385380    0.000000    0.000000   
ENSG00000160193   24.552405   22.505395   22.286025   21.982311   21.548097   
ENSG00000160194   16.568086   15.492327   15.341720   15.218094   15.202386   
ENSG00000160199   13.131905   12.889644   12.492341   12.434685   12.229141   
ENSG00000160200    0.167474    0.145870    0.137995    0.131724    0.126463   
ENSG00000162924  322.078644  315.519847  278.386292  271.381439  249.348238   
ENSG00000162927   76.504159   73.564193   68.574112   57.563111   57.127143   
ENSG00000162928   15.573790   14.546541   14.259838   13.845456   13.317065 

In [71]:
for cline in diceweb_to_loop_names.values():
    tdf = compare_df.loc[compare_df.cline == cline]
    break

In [73]:
tdf.pivot(columns='type')

0                       1                       2  \
type                  coloc         sgl       coloc         sgl       coloc   
Feature_name                                                                  
ENSG00000004866    1.477158         NaN    1.228522         NaN    0.954731   
ENSG00000025039    2.821166         NaN    2.643562         NaN    2.456848   
ENSG00000026950  235.245405         NaN  226.275791         NaN  221.714012   
ENSG00000065675    1.092529         NaN    1.020098         NaN    0.948681   
ENSG00000079739   13.691564         NaN   13.387624         NaN   12.960432   
ENSG00000080298   36.145947         NaN   36.105101         NaN   35.353010   
ENSG00000081026    2.026828         NaN    1.159936         NaN    1.116276   
ENSG00000089022   28.483846         NaN   26.938844         NaN   26.770207   
ENSG00000090104         NaN  795.377644         NaN  652.258790         NaN   
ENSG00000096433  106.765367         NaN   99.444632         NaN   96.530323   
ENSG00000106686    0.919483         NaN    0.884847         NaN    0.860963   
ENSG00000107249    0.028137         NaN    0.028069         NaN    0.000000   
ENSG00000107796    5.670728         NaN    5.659299         NaN    5.637337   
ENSG00000110665  163.908274         NaN  156.108806         NaN  124.275407   
ENSG00000111231   16.448997         NaN   15.557383         NaN   12.075021   
ENSG00000111275    8.393630         NaN    7.750443         NaN    7.712299   
ENSG00000111300         NaN   75.066008         NaN   71.424736         NaN   
ENSG00000111802   63.990051         NaN   63.338166         NaN   62.567352   
ENSG00000111886   31.589619         NaN   18.750681         NaN   15.274571   
ENSG00000112182  339.309849         NaN  324.581740         NaN  322.543162   
ENSG00000112293    5.769111         NaN    5.381150         NaN    5.196450   
ENSG00000112312   11.861967         NaN   10.921975         NaN   10.046572   
ENSG00000112679  129.236326         NaN  128.688319         NaN  126.826483   
ENSG00000115421   37.158713         NaN   37.077836         NaN   35.738083   
ENSG00000119866  142.909793         NaN  131.478191         NaN  131.173091   
ENSG00000124508  113.321745         NaN  110.152844         NaN  110.082968   
ENSG00000124610         NaN    0.595489         NaN    0.504677         NaN   
ENSG00000128534  109.016716         NaN  101.258497         NaN   96.861194   
ENSG00000132436   53.305219         NaN   48.325893         NaN   45.928951   
ENSG00000133466   33.376542         NaN   32.896560         NaN   32.120393   
ENSG00000134242  177.158906         NaN  160.580860         NaN  158.389564   
ENSG00000134453         NaN  123.536939         NaN  119.687642         NaN   
ENSG00000134460         NaN   19.432292         NaN   18.766306         NaN   
ENSG00000135299    3.259571         NaN    2.704862         NaN    2.626511   
ENSG00000135341   51.111087         NaN   50.001180         NaN   49.655038   
ENSG00000136982    4.203182         NaN    3.497860         NaN    3.084255   
ENSG00000138685    2.999023         NaN    2.449939         NaN    2.229621   
ENSG00000138686   19.253795         NaN   16.229995         NaN   15.771540   
ENSG00000139531    4.077676         NaN    3.882161         NaN    3.496302   
ENSG00000141956   16.243744         NaN   14.646146         NaN   14.607680   
ENSG00000146281   60.631776         NaN   58.282220         NaN   56.968573   
ENSG00000150637    0.806597         NaN    0.760199         NaN    0.675722   
ENSG00000152766    0.366447         NaN    0.346577         NaN    0.256330   
ENSG00000157617   19.813242         NaN   17.913322         NaN   17.510008   
ENSG00000158966    0.906131         NaN    0.695685         NaN    0.640453   
ENSG00000160179   63.006539         NaN   50.920611         NaN   48.826939   
ENSG00000160181    1.189608         NaN    1.026941         NaN    0.385380   
ENSG00000160183         NaN    0.434305         NaN    0.416960         NaN 

In [118]:
for rsid in compiled_sgls.rs_id.unique().tolist():
    print(rsid)

rs7090530
rs706779
rs10850001
rs7300285
rs10801128
rs7072793
rs9981624
rs9366622
rs56297233
rs10876864
rs1131017
rs674222
rs231724


In [130]:
compiled_sgls.loc[compiled_sgls.genename == 'RPS26']

chr  snp_start   snp_end    chr  gene_start  gene_end  \
210  chr12   56412486  56412487  chr12    56435135  56435136   
190  chr12   56412486  56412487  chr12    56435135  56435136   
154  chr12   56412486  56412487  chr12    56435135  56435136   
156  chr12   56412486  56412487  chr12    56435135  56435136   
248  chr12   56416927  56416928  chr12    56435135  56435136   
238  chr12   56416927  56416928  chr12    56435135  56435136   
220  chr12   56416927  56416928  chr12    56435135  56435136   
221  chr12   56416927  56416928  chr12    56435135  56435136   

                                                                 coloc_id  \
210                  chr12.56412487.RPS26.T1D_32005708.BLUEPRINT.monocyte   
190                   chr12.56412487.RPS26.T1D_32005708.ImmuNexUT.CL_Mono   
154  chr12.56412487.RPS26.T1D_32005708.Schmiedel_2018.monocyte_CD16_naive   
156       chr12.56412487.RPS26.T1D_32005708.Schmiedel_2018.monocyte_naive   
248                  chr12.56416928.RPS26.T1D_32005708.BLUEPRINT.monocyte   
238                   chr12.56416928.RPS26.T1D_32005708.ImmuNexUT.CL_Mono   
220  chr12.56416928.RPS26.T1D_32005708.Schmiedel_2018.monocyte_CD16_naive   
221       chr12.56416928.RPS26.T1D_32005708.Schmiedel_2018.monocyte_naive   

    loop_chrA  loop_startA  loop_endA loop_chrB  loop_startB  loop_endB  \
210     chr12     56410000   56415000     chr12     56435000   56440000   
190     chr12     56410000   56415000     chr12     56435000   56440000   
154     chr12     56410000   56415000     chr12     56435000   56440000   
156     chr12     56410000   56415000     chr12     56435000   56440000   
248     chr12     56410000   56415000     chr12     56435000   56440000   
238     chr12     56410000   56415000     chr12     56435000   56440000   
220     chr12     56410000   56415000     chr12     56435000   56440000   
221     chr12     56410000   56415000     chr12     56435000   56440000   

                                             loop_id sgl_kind       pos  \
210  chr12.56410000.56415000.chr12.56435000.56440000      tss  56412487   
190  chr12.56410000.56415000.chr12.56435000.56440000      tss  56412487   
154  chr12.56410000.56415000.chr12.56435000.56440000      tss  56412487   
156  chr12.56410000.56415000.chr12.56435000.56440000      tss  56412487   
248  chr12.56410000.56415000.chr12.56435000.56440000      tss  56416928   
238  chr12.56410000.56415000.chr12.56435000.56440000      tss  56416928   
220  chr12.56410000.56415000.chr12.56435000.56440000      tss  56416928   
221  chr12.56410000.56415000.chr12.56435000.56440000      tss  56416928   

     pp_H0_Coloc_Summary  pp_H1_Coloc_Summary  pp_H2_Coloc_Summary  \
210                  0.0                  0.0         5.046047e-08   
190                  0.0                  0.0         3.695862e-08   
154                  0.0                  0.0         3.451621e-08   
156                  0.0                  0.0         3.443134e-08   
248                  0.0                  0.0         5.046047e-08   
238                  0.0                  0.0         3.695862e-08   
220                  0.0                  0.0         3.451621e-08   
221                  0.0                  0.0         3.443134e-08   

     pp_H3_Coloc_Summary  pp_H4_Coloc_Summary       rs_id       variant_id  \
210             0.224853             0.775147  rs10876864  12:56007301:G:A   
190             0.198122             0.801877   rs1131017  12:56042145:C:G   
154             0.213262             0.786738   rs1131017  12:56042145:C:G   
156             0.209550             0.790450   rs1131017  12:56042145:C:G   
248             0.224853             0.775147  rs10876864  12:56007301:G:A   
238             0.198122             0.801877   rs1131017  12:56042145:C:G   
220             0.213262             0.786738   rs1131017  12:56042145:C:G   
221             0.209550             0.790450   rs1131017  12:56042145:C:G   

      geneid_versioned   dist        pvalue       

In [141]:
t = compiled_sgls[['genename', 'rs_id', 'pvalue', 'FDR', 'eqtl_source', 'ge_source', 'loop_source']]

In [143]:
t = t.drop_duplicates()

In [145]:
t[t.genename == 'IL2RA']

genename      rs_id        pvalue           FDR eqtl_source ge_source  \
216    IL2RA  rs7090530  7.242360e-11  1.969261e-08   ImmuNexUT      DN_B   
207    IL2RA  rs7090530  5.046700e-12  1.325424e-09   ImmuNexUT      SM_B   
212    IL2RA  rs7090530  2.433710e-20  1.710702e-17   ImmuNexUT     USM_B   
209    IL2RA   rs706779  9.850680e-15  3.835600e-12   ImmuNexUT   Naive_B   

      loop_source  
216  B-cell_naive  
207  B-cell_naive  
212  B-cell_naive  
209  B-cell_naive

In [186]:
compiled_sgls.loc[compiled_sgls.iloc[:, 0] == 'chr18', :]

chr  snp_start   snp_end    chr  gene_start  gene_end  \
287  chr18   12876392  12876393  chr18    11857552  11857553   
288  chr18   12876396  12876397  chr18    11857552  11857553   
286  chr18   12882358  12882359  chr18    11857552  11857553   
285  chr18   12884342  12884343  chr18    11857552  11857553   

                                                                coloc_id  \
287  chr18.12876393.AP005137.2.T1D_25751624.Quach_2016.monocyte_Pam3CSK4   
288  chr18.12876397.AP005137.2.T1D_25751624.Quach_2016.monocyte_Pam3CSK4   
286  chr18.12882359.AP005137.2.T1D_25751624.Quach_2016.monocyte_Pam3CSK4   
285  chr18.12884343.AP005137.2.T1D_25751624.Quach_2016.monocyte_Pam3CSK4   

    loop_chrA  loop_startA  loop_endA loop_chrB  loop_startB  loop_endB  \
287     chr18     11850000   11855000     chr18     12880000   12885000   
288     chr18     11850000   11855000     chr18     12880000   12885000   
286     chr18     11850000   11855000     chr18     12880000   12885000   
285     chr18     11850000   11855000     chr18     12880000   12885000   

                                             loop_id sgl_kind       pos  \
287  chr18.11850000.11855000.chr18.12880000.12885000      tss  12876393   
288  chr18.11850000.11855000.chr18.12880000.12885000      tss  12876397   
286  chr18.11850000.11855000.chr18.12880000.12885000      tss  12882359   
285  chr18.11850000.11855000.chr18.12880000.12885000      tss  12884343   

     pp_H0_Coloc_Summary  pp_H1_Coloc_Summary  pp_H2_Coloc_Summary  \
287         4.293501e-08             0.000032             0.000281   
288         4.293501e-08             0.000032             0.000281   
286         4.293501e-08             0.000032             0.000281   
285         4.293501e-08             0.000032             0.000281   

     pp_H3_Coloc_Summary  pp_H4_Coloc_Summary     rs_id       variant_id  \
287             0.211098             0.788588  rs674222  18:12848350:G:C   
288             0.211098             0.788588  rs674222  18:12848350:G:C   
286             0.211098             0.788588  rs674222  18:12848350:G:C   
285             0.211098             0.788588  rs674222  18:12848350:G:C   

    geneid_versioned    dist   pvalue       FDR  slope_snp ref alt    AC  \
287  ENSG00000272703  990796  0.00708  0.335277   0.219838   G   C  1128   
288  ENSG00000272703  990796  0.00708  0.335277   0.219838   G   C  1128   
286  ENSG00000272703  990796  0.00708  0.335277   0.219838   G   C  1128   
285  ENSG00000272703  990796  0.00708  0.335277   0.219838   G   C  1128   

          AF    AN  slope_se_snp  slope_gwas  slope_se_gwas  pval_nominal  \
287  0.22524  5008      0.033347   -0.143986       0.018998  3.480000e-14   
288  0.22524  5008      0.033347   -0.143986       0.018998  3.480000e-14   
286  0.22524  5008      0.033347   -0.143986       0.018998  3.480000e-14   
285  0.22524  5008      0.033347   -0.143986       0.018998  3.480000e-14   

      old_pos  was_converted      rsID ld_chr    ld_pos     ld_rsID        LD  \
287  12848350              1  rs674222  chr18  12876393   rs5823237  0.994300   
288  12848350              1  rs674222  chr18  12876397  rs63746461  0.994300   
286  12848350              1  rs674222  chr18  12882359   rs4797709  0.991836   
285  12848350              1  rs674222  chr18  12884343   rs2292759  0.991746   

      gwas_source eqtl_source          ge_source  SampleSize  coloc_pos  \
287  T1D_25751624  Quach_2016  monocyte_Pam3CSK4         NaN   12848349   
288  T1D_25751624  Quach_2016  monocyte_Pam3CSK4         NaN   12848349   
286  T1D_25751624  Quach_2016  monocyte_Pam3CSK4         NaN   12848349   
285  T1D_25751624  Quach_2016  monocyte_Pam3CSK4         NaN   12848349   

              geneid gene_strand    genename  tss_start   tss_end   chr1  \
287  ENSG00000272703           -  AP005137.2   11857552  11857553  chr18   
288  ENSG00000272703           -  AP005137.2   11857552  11857553  chr18   
286  ENSG00000272703           -  AP005137.2

In [187]:
compiled_sgls.loc[compiled_sgls.genename == 'IL2RA']

chr  snp_start  snp_end    chr  gene_start  gene_end  \
216  chr10    6110828  6110829  chr10     6052652   6104333   
237  chr10    6110828  6110829  chr10     6052652   6104333   
278  chr10    6110828  6110829  chr10     6104332   6104333   
207  chr10    6110828  6110829  chr10     6052652   6104333   
228  chr10    6110828  6110829  chr10     6052652   6104333   
260  chr10    6110828  6110829  chr10     6104332   6104333   
212  chr10    6110828  6110829  chr10     6052652   6104333   
233  chr10    6110828  6110829  chr10     6052652   6104333   
270  chr10    6110828  6110829  chr10     6104332   6104333   
203  chr10    6110828  6110829  chr10     6052652   6104333   
224  chr10    6110828  6110829  chr10     6052652   6104333   
252  chr10    6110828  6110829  chr10     6104332   6104333   
199  chr10    6110828  6110829  chr10     6052652   6104333   
220  chr10    6110828  6110829  chr10     6052652   6104333   
244  chr10    6110828  6110829  chr10     6104332   6104333   
217  chr10    6110874  6110875  chr10     6052652   6104333   
238  chr10    6110874  6110875  chr10     6052652   6104333   
280  chr10    6110874  6110875  chr10     6104332   6104333   
208  chr10    6110874  6110875  chr10     6052652   6104333   
229  chr10    6110874  6110875  chr10     6052652   6104333   
262  chr10    6110874  6110875  chr10     6104332   6104333   
213  chr10    6110874  6110875  chr10     6052652   6104333   
234  chr10    6110874  6110875  chr10     6052652   6104333   
272  chr10    6110874  6110875  chr10     6104332   6104333   
204  chr10    6110874  6110875  chr10     6052652   6104333   
225  chr10    6110874  6110875  chr10     6052652   6104333   
254  chr10    6110874  6110875  chr10     6104332   6104333   
200  chr10    6110874  6110875  chr10     6052652   6104333   
221  chr10    6110874  6110875  chr10     6052652   6104333   
246  chr10    6110874  6110875  chr10     6104332   6104333   
215  chr10    6113781  6113782  chr10     6052652   6104333   
236  chr10    6113781  6113782  chr10     6052652   6104333   
276  chr10    6113781  6113782  chr10     6104332   6104333   
206  chr10    6113781  6113782  chr10     6052652   6104333   
227  chr10    6113781  6113782  chr10     6052652   6104333   
258  chr10    6113781  6113782  chr10     6104332   6104333   
211  chr10    6113781  6113782  chr10     6052652   6104333   
232  chr10    6113781  6113782  chr10     6052652   6104333   
268  chr10    6113781  6113782  chr10     6104332   6104333   
202  chr10    6113781  6113782  chr10     6052652   6104333   
223  chr10    6113781  6113782  chr10     6052652   6104333   
250  chr10    6113781  6113782  chr10     6104332   6104333   
198  chr10    6113781  6113782  chr10     6052652   6104333   
219  chr10    6113781  6113782  chr10     6052652   6104333   
242  chr10    6113781  6113782  chr10     6104332   6104333   
214  chr10    6114009  6114010  chr10     6052652   6104333   
235  chr10    6114009  6114010  chr10     6052652   6104333   
274  chr10    6114009  6114010  chr10     6104332   6104333   
205  chr10    6114009  6114010  chr10     6052652   6104333   
226  chr10    6114009  6114010  chr10     6052652   6104333   
256  chr10    6114009  6114010  chr10     6104332   6104333   
210  chr10    6114009  6114010  chr10     6052652   6104333   
231  chr10    6114009  6114010  chr10     6052652   6104333   
266  chr10    6114009  6114010  chr10     6104332   6104333   
201  chr10    6114009  6114010  chr10     6052652   6104333   
222  chr10    6114009  6114010  chr10     6052652   6104333   
248  chr10    6114009  6114010  chr10     6104332   6104333   
197  chr10    6114009  6114010  chr10     6052652   6104333   
218  chr10    6114009  6114010  chr10     6052652   6104333   
240  chr10    6114009  6114010  chr10     6104332   6104333   
209  chr10    6114292  6114293  chr10     6052652   6104333   
230  chr10    6114292  6114293  chr10     6052652   6104333   
264  chr10    6114292  6114293  chr10 